In [1]:
import time 
import requests
import cv2
import operator
import numpy as np
from __future__ import print_function

# Import library to display results
import matplotlib.pyplot as plt
%matplotlib inline 
# Display images within Jupyter

In [2]:
_url = 'https://api.projectoxford.ai/face/v1.0/detect'
_key = '89493f7b061f47fba871939e0117a807'
_maxNumRetries = 10

malePath   = '/home/maru/Project/modu/label/male/'
femalePath = '/home/maru/Project/modu/label/female/'
etcPath    = '/home/maru/Project/modu/label/etc/'

In [3]:
def processRequest( json, data, headers, params ):

    """
    Helper function to process the request to Project Oxford

    Parameters:
    json: Used when processing images from its URL. See API Documentation
    data: Used when processing image read from disk. See API Documentation
    headers: Used to pass the key information and the data type request
    """

    retries = 0
    result = None

    while True:

        response = requests.request( 'post', _url, json = json, data = data, headers = headers, params = params )

        if response.status_code == 429: 

            print( "Message: %s" % ( response.json()['error']['message'] ) )

            if retries <= _maxNumRetries: 
                time.sleep(1) 
                retries += 1
                continue
            else: 
                print( 'Error: failed after retrying!' )
                break

        elif response.status_code == 200 or response.status_code == 201:

            if 'content-length' in response.headers and int(response.headers['content-length']) == 0: 
                result = None 
            elif 'content-type' in response.headers and isinstance(response.headers['content-type'], str): 
                if 'application/json' in response.headers['content-type'].lower(): 
                    result = response.json() if response.content else None 
                elif 'image' in response.headers['content-type'].lower(): 
                    result = response.content
        else:
            print( "Error code: %d" % ( response.status_code ) )
            print( "Message: %s" % ( response.json()['error']['message'] ) )

        break
        
    return result

In [4]:
def saveImage(img, label, filename, count):
    if label is not None:
        if label == 'male' :
            cv2.imwrite(malePath + str(count) + '_' + filename, img)
        elif label == 'female':
            cv2.imwrite(femalePath + str(count) + '_' + filename, img)
        else:
             cv2.imwrite(etcPath + str(count) + '_' + filename, img)\
        
        print ("save complate : ") , (filename)

In [5]:
def resultImage( result, img, filename ):
    count = 0
    for currFace in result:
        faceRectangle = currFace['faceRectangle']
        cv2.rectangle( img,(faceRectangle['left'],faceRectangle['top']),
                           (faceRectangle['left']+faceRectangle['width'], faceRectangle['top'] + faceRectangle['height']),
                       color = (255,0,0), thickness = 1 )

        faceLandmarks = currFace['faceLandmarks']
        
        x = faceRectangle['left']
        y = faceRectangle['top']
        w = faceRectangle['width']
        h = faceRectangle['height']
        
        roi = img[ y : y + h, x : x + w ]
        
        gender = currFace['faceAttributes']['gender']
                
        saveImage(roi, gender, filename, count)
        
        count = count + 1

In [6]:
def genderLabel(full_path, filename):
    # Load raw image file into memory
    pathToFileInDisk = full_path
    with open( pathToFileInDisk, 'rb' ) as f:
        data = f.read()

    # Face detection parameters
    params = { 'returnFaceAttributes': 'age,gender', 
               'returnFaceLandmarks': 'true'} 

    headers = dict()
    headers['Ocp-Apim-Subscription-Key'] = _key
    headers['Content-Type'] = 'application/octet-stream'

    json = None

    result = processRequest( json, data, headers, params )
    
    if result is not None:

        # Load the original image from disk
        data8uint = np.fromstring( data, np.uint8 ) # Convert string to an unsigned int array
        #img = cv2.cvtColor( cv2.imdecode( data8uint, cv2.IMREAD_COLOR ), cv2.COLOR_BGR2RGB )
        img = cv2.imdecode( data8uint, cv2.IMREAD_COLOR )
        resultImage( result, img, filename )
        

In [15]:
def search(dirname):
    if os.path.isdir(dirname):
        
        filenames = os.listdir(dirname)
        print (filenames)
        for filename in filenames:
            full_filename = os.path.join(dirname, filename)
            if os.path.isdir(full_filename):
                search(full_filename)
            else:
                ext = os.path.splitext(full_filename)[-1]
                if ext == '.jpg' or ext == '.png':                 
                    t=[]
                    t.append(full_filename)
                    t.append(filename)
                    res.append(t)       
        return res
    

In [16]:
import os
pwd = '/home/maru/Project/modu/data'
res = search(pwd)

['300W', 'helen', 'CK+', 'LFPW+wild', 'AFLW']
['02_Outdoor', '01_Indoor']
['outdoor_148.pts', 'outdoor_096.png', 'outdoor_101.png', 'outdoor_285.png', 'outdoor_290.pts', 'outdoor_109.png', 'outdoor_099.pts', 'outdoor_253.png', 'outdoor_263.png', 'outdoor_170.png', 'outdoor_253.pts', 'outdoor_134.pts', 'outdoor_096.pts', 'outdoor_015.pts', 'outdoor_023.png', 'outdoor_074.pts', 'outdoor_250.png', 'outdoor_042.pts', 'outdoor_095.pts', 'outdoor_066.pts', 'outdoor_092.pts', 'outdoor_169.pts', 'outdoor_264.png', 'outdoor_079.png', 'outdoor_167.png', 'outdoor_243.png', 'outdoor_135.png', 'outdoor_292.pts', 'outdoor_289.png', 'outdoor_060.png', 'outdoor_140.pts', 'outdoor_027.pts', 'outdoor_033.png', 'outdoor_063.pts', 'outdoor_066.png', 'outdoor_053.png', 'outdoor_028.pts', 'outdoor_270.pts', 'outdoor_176.png', 'outdoor_231.png', 'outdoor_103.png', 'outdoor_164.png', 'outdoor_112.pts', 'outdoor_297.pts', 'outdoor_122.png', 'outdoor_086.pts', 'outdoor_087.pts', 'outdoor_151.pts', 'outdoor_220.

In [17]:
print (res)

[['/home/maru/Project/modu/data/300W/02_Outdoor/outdoor_096.png', 'outdoor_096.png'], ['/home/maru/Project/modu/data/300W/02_Outdoor/outdoor_101.png', 'outdoor_101.png'], ['/home/maru/Project/modu/data/300W/02_Outdoor/outdoor_285.png', 'outdoor_285.png'], ['/home/maru/Project/modu/data/300W/02_Outdoor/outdoor_109.png', 'outdoor_109.png'], ['/home/maru/Project/modu/data/300W/02_Outdoor/outdoor_253.png', 'outdoor_253.png'], ['/home/maru/Project/modu/data/300W/02_Outdoor/outdoor_263.png', 'outdoor_263.png'], ['/home/maru/Project/modu/data/300W/02_Outdoor/outdoor_170.png', 'outdoor_170.png'], ['/home/maru/Project/modu/data/300W/02_Outdoor/outdoor_023.png', 'outdoor_023.png'], ['/home/maru/Project/modu/data/300W/02_Outdoor/outdoor_250.png', 'outdoor_250.png'], ['/home/maru/Project/modu/data/300W/02_Outdoor/outdoor_264.png', 'outdoor_264.png'], ['/home/maru/Project/modu/data/300W/02_Outdoor/outdoor_079.png', 'outdoor_079.png'], ['/home/maru/Project/modu/data/300W/02_Outdoor/outdoor_167.png',

In [19]:
for i in range(len(res)):
    full_path = res[i][0]
    filename = res[i][1]
    
    print (full_path)
    print (filename)
    
    genderLabel(full_path, filename)

/home/maru/Project/modu/data/300W/02_Outdoor/outdoor_096.png
outdoor_096.png
Error code: 400
Message: Image size is too small or too big.
/home/maru/Project/modu/data/300W/02_Outdoor/outdoor_101.png
outdoor_101.png
Error code: 400
Message: Image size is too small or too big.
/home/maru/Project/modu/data/300W/02_Outdoor/outdoor_285.png
outdoor_285.png
save complate : 
/home/maru/Project/modu/data/300W/02_Outdoor/outdoor_109.png
outdoor_109.png
save complate : 
save complate : 
save complate : 
save complate : 
save complate : 
save complate : 
save complate : 
/home/maru/Project/modu/data/300W/02_Outdoor/outdoor_253.png
outdoor_253.png
save complate : 
/home/maru/Project/modu/data/300W/02_Outdoor/outdoor_263.png
outdoor_263.png
save complate : 
/home/maru/Project/modu/data/300W/02_Outdoor/outdoor_170.png
outdoor_170.png
Error code: 400
Message: Image size is too small or too big.
/home/maru/Project/modu/data/300W/02_Outdoor/outdoor_023.png
outdoor_023.png
Error code: 400
Message: Image 

ConnectionError: HTTPSConnectionPool(host='api.projectoxford.ai', port=443): Max retries exceeded with url: /face/v1.0/detect?returnFaceAttributes=age%2Cgender&returnFaceLandmarks=true (Caused by NewConnectionError('<requests.packages.urllib3.connection.VerifiedHTTPSConnection object at 0x7f2f3358b510>: Failed to establish a new connection: [Errno -2] Name or service not known',))